### Create window aggregate features 

Next feature type we will consider is window aggregate feature. 
These are features generated by aggregating data within specific time frame.  


In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

16:07:43 | WARNING  | Service endpoint is inaccessible: http://featurebyte-server:8088


16:07:43 | INFO     | Using profile: tutorial


16:07:43 | INFO     | Using configuration file at: /Users/gxav/.featurebyte/config.yaml


16:07:43 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


16:07:43 | WARNING  | Remote SDK version (1.1.0.dev7) is different from local (1.1.0.dev1). Update local SDK to avoid unexpected behavior.


16:07:43 | INFO     | No catalog activated.


16:07:43 | INFO     | Catalog activated: Grocery Dataset Tutorial


In [2]:
# Set desired windows
windows = ['14d', '28d']

#### Do window aggregation from INVOICEITEMS

Let's start with some aggregations from the items view and create features for the interaction between Customer and Product Group. 

In [3]:
# Get view from GROCERYPRODUCT dimension table.
groceryproduct_view = catalog.get_view("GROCERYPRODUCT")
# Get view from INVOICEITEMS item table.
invoiceitems_view = catalog.get_view("INVOICEITEMS")
# Join GROCERYPRODUCT view to INVOICEITEMS view.
invoiceitems_view = invoiceitems_view.join(groceryproduct_view, rsuffix="")

In [4]:
# Group GROCERYINVOICE view by customer entity (GroceryCustomerGuid) and productgroup entity (ProductGroup).
invoiceitems_view_by_customer_x_productgroup = invoiceitems_view.groupby(
    ['GroceryCustomerGuid', 'ProductGroup']
)

In [5]:
# Get Sum of TotalCost for the customer x productgroup over time.
customer_productgroup_sum_of_totalcost_14d_28d = \
invoiceitems_view_by_customer_x_productgroup.aggregate_over(
    "TotalCost", method="sum",
    feature_names=[
        "CUSTOMER_x_PRODUCTGROUP_Sum_of_item_TotalCost"
        + "_" + w for w in windows
    ],
    windows=windows
)

In [6]:
# Get Latest Interaction between Customer and ProductGroup
customer_x_productgroup_latest_timestamp = \
invoiceitems_view_by_customer_x_productgroup.aggregate_over(
    "Timestamp", method="latest",
    feature_names=["CUSTOMER_x_PRODUCTGROUP_Latest_Timestamp"],
    windows=[None]
)["CUSTOMER_x_PRODUCTGROUP_Latest_Timestamp"]

In [7]:
# Create recency feature: Time Since Latest Interaction between Customer and Product Group
customer_x_productgroup_time_since_latest_timestamp = (
    fb.RequestColumn.point_in_time()
    - customer_x_productgroup_latest_timestamp
).dt.hour
customer_x_productgroup_time_since_latest_timestamp.name = \
"CUSTOMER_x_PRODUCTGROUP_Time_Since_Latest_Timestamp"

#### Do window aggregation from GROCERYINVOICE

Now, let's do some aggregations on the invoices view for the Customer entity.

In [8]:
# Get view from GROCERYINVOICE event table.
groceryinvoice_view = catalog.get_view("GROCERYINVOICE")

In [9]:
# Group GROCERYINVOICE view by customer entity (GroceryCustomerGuid).
groceryinvoice_view_by_customer = groceryinvoice_view.groupby(['GroceryCustomerGuid'])

In [10]:
# Get Latest invoice Amount for the customer
customer_latest_invoice_amount = groceryinvoice_view_by_customer.aggregate_over(
    "Amount", method="latest",
    feature_names=["CUSTOMER_Latest_invoice_Amount"],
    windows=[None]
)["CUSTOMER_Latest_invoice_Amount"]

In [11]:
# Get Count of invoices for the customer
customer_count_of_invoice_14d_28d = groceryinvoice_view_by_customer.aggregate_over(
    value_column=None,
    method="count",
    feature_names=[
        "CUSTOMER_Count_of_invoice"
        + "_" + w for w in windows
    ],
    windows=windows
)

In [12]:
# Get Avg of Amount for the customer over time.
customer_avg_of_invoice_amount_14d_28d = groceryinvoice_view_by_customer.aggregate_over(
    "Amount", method="avg",
    feature_names=[
        "CUSTOMER_Avg_of_invoice_Amount"
        + "_" + w for w in windows
    ],
    windows=windows
)

In [13]:
# Get Std of Amount for the customer over time.
customer_std_of_invoice_amount_14d_28d = groceryinvoice_view_by_customer.aggregate_over(
    "Amount", method="std",
    feature_names=[
        "CUSTOMER_Std_of_invoice_Amount"
        + "_" + w for w in windows
    ],
    windows=windows
)

#### Preview a feature group
For convenience, we can create a feature group to preview/save all features we just created.

In [14]:
feature_group = fb.FeatureGroup([
    customer_x_productgroup_time_since_latest_timestamp,
    customer_productgroup_sum_of_totalcost_14d_28d,
    customer_latest_invoice_amount,
    customer_count_of_invoice_14d_28d,
    customer_avg_of_invoice_amount_14d_28d,
    customer_std_of_invoice_amount_14d_28d,
])

In [15]:
# Check the primary entity of the feature group. It should be the interaction Customer x ProductGroup.
feature_group.primary_entity

 {
   'name': 'customer',
   'created_at': '2024-06-12T08:05:47.417000',
   'updated_at': '2024-06-12T08:05:50.497000',
   'description': None,
   'serving_names': [
     'GROCERYCUSTOMERGUID'
   ],
   'catalog_name': 'Grocery Dataset Tutorial'
 },
 {
   'name': 'productgroup',
   'created_at': '2024-06-12T08:05:48.244000',
   'updated_at': '2024-06-12T08:05:51.678000',
   'description': None,
   'serving_names': [
     'PRODUCTGROUP'
   ],
   'catalog_name': 'Grocery Dataset Tutorial'
 }]

In [16]:
# Get observation table: 'Preview Table with 10 items'
preview_table = catalog.get_observation_table("Preview Table with 10 items")

In [17]:
# Preview feature_group
feature_group.preview(preview_table)

POINT_IN_TIME                GROCERYINVOICEITEMGUID  \
0 2023-05-28 19:27:14  15973b2f-2256-4caa-b65b-cbbfdff0905b   
1 2023-02-07 11:04:26  fd1caae1-77e6-4667-8c83-df13f05bf2f5   
2 2023-03-31 18:50:00  213ef7d3-c27b-43e0-bc0a-57d6c7c254b0   
3 2022-09-18 18:52:36  ac7edfb5-63ed-49fb-9b89-76b0288ed2f8   
4 2022-12-26 15:01:07  264f79fd-c24a-47cc-8a68-fe3753a4d74b   
5 2022-08-17 19:13:52  40a07ca4-a991-4d21-b5cf-74ee61220f96   
6 2023-04-11 17:23:57  6084f39f-9d2c-4111-b1cc-502e1559c0c0   
7 2022-12-10 21:08:26  77d02174-f1e1-41c1-9fb9-01c6246b0009   
8 2023-03-17 11:15:09  1b627a25-7eb4-4f61-b243-c93db487bff0   
9 2023-05-05 08:00:42  57ca0770-eb8b-4769-8e67-eb1b7cc0a934   

   CUSTOMER_x_PRODUCTGROUP_Time_Since_Latest_Timestamp  \
0                                        1106.468611     
1                                         360.113056     
2                                         269.623333     
3                                          99.261667     
4                                          73.213056     
5                                         343.933611     
6                                         197.481944     
7                                                NaN     
8                                         140.312500     
9                                        1097.448611     

   CUSTOMER_x_PRODUCTGROUP_Sum_of_item_TotalCost_14d  \
0                                                NaN   
1                                                NaN   
2                                               8.00   
3                                              16.63   
4                                               6.28   
5                                                NaN   
6                                               6.00   
7                                                NaN   
8                                               1.67   
9                                                NaN   

   CUSTOMER_x_PRODUCTGROUP_Sum_of_item_TotalCost_28d  \
0                                                NaN   
1                                               8.28   
2                                               8.00   
3                                              24.13   
4                                              14.46   
5                                               6.00   
6                                               6.00   
7                                                NaN   
8                                               1.67   
9                                                NaN   

   CUSTOMER_Latest_invoice_Amount  CUSTOMER_Count_of_invoice_14d  \
0                            4.17                            1.0   
1                           36.35                            1.0   
2                           53.11                            1.0   
3                           95.05                            6.0   
4                           39.25                            1.0   
5                           34.27                            NaN   
6                           19.70                            2.0   
7                           31.73                            1.0   
8                            9.82                            5.0   
9                            8.47                            2.0   

   CUSTOMER_Count_of_invoice_28d  CUSTOMER_Avg_of_invoice_Amount_14d  \
0                              1                               4.170   
1                              3                              36.350   
2                              1                              53.110   
3                             12                              34.825   
4                              6                              39.250   
5                              4                                 NaN   
6                              2                              18.490   
7                              1                              31.730   
8                              6            

#### Save features into catalog 
With feature groups we can do it in one call.

In [18]:
feature_group.save()

Working... |                                        | ▁▃▅ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▂▄▆ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▃▅▇ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▄▆█ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▅▇▇ 0% in 0s (~0s, 0.0%/s)

...

Loading Feature(s) |                                        | ▁▃▅ 0/10 [0%] in 0

Loading Feature(s) |                                        | ▂▄▆ 0/10 [0%] in 0

Loading Feature(s) |                                        | ▃▅▇ 0/10 [0%] in 0

Loading Feature(s) |████████████████████████████████████████| ▄▆█ 10/10 [100%] i

Loading Feature(s) |████████████████████████████████████████| 10/10 [100%] in 0.

#### Add description and see feature definition files

In [19]:
# Add description
customer_x_productgroup_time_since_latest_timestamp.update_description(
    "Time Since Latest interaction between the customer and the product group"
)
# See feature definition file
customer_x_productgroup_time_since_latest_timestamp.definition

'# Generated by SDK version: 1.1.0.dev7\nfrom bson import ObjectId\nfrom featurebyte import DimensionTable\nfrom featurebyte import FeatureJobSetting\nfrom featurebyte import ItemTable\nfrom featurebyte.api.request_column import RequestColumn\n\n\n# dimension_table name: "GROCERYPRODUCT"\ndimension_table = DimensionTable.get_by_id(ObjectId("666956c78080c62d0dc616e2"))\ndimension_view = dimension_table.get_view(\n    view_mode="manual", drop_column_names=[], column_cleaning_operations=[]\n)\n\n# item_table name: "INVOICEITEMS", event_table name: "GROCERYINVOICE"\nitem_table = ItemTable.get_by_id(ObjectId("666956c58080c62d0dc616e1"))\nitem_view = item_table.get_view(\n    event_suffix=None,\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[],\n    event_drop_column_names=["record_available_at"],\n    event_column_cleaning_operations=[],\n    event_join_column_names=[\n        "Timestamp",\n        "GroceryInvoiceGuid",\n        "GroceryCustomerGuid",\n        "tz_offset",\n    ],\n)\njoined_view = item_view.join(\n    dimension_view, on="GroceryProductGuid", how="left", rsuffix="", rprefix=""\n)\ngrouped = joined_view.groupby(\n    by_keys=["GroceryCustomerGuid", "ProductGroup"], category=None\n).aggregate_over(\n    value_column="Timestamp",\n    method="latest",\n    windows=[None],\n    feature_names=["CUSTOMER_x_PRODUCTGROUP_Latest_Timestamp"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", period="3600s", offset="120s"\n    ),\n    skip_fill_na=True,\n    offset=None,\n)\nfeat = grouped["CUSTOMER_x_PRODUCTGROUP_Latest_Timestamp"]\nrequest_col = RequestColumn.point_in_time()\nfeat_1 = (request_col - feat).dt.hour\nfeat_1.name = "CUSTOMER_x_PRODUCTGROUP_Time_Since_Latest_Timestamp"\noutput = feat_1\noutput.save(_id=ObjectId("6669575033eb5cd5aebc1fe9"))\n'

In [20]:
# Add description
customer_productgroup_sum_of_totalcost_14d = \
customer_productgroup_sum_of_totalcost_14d_28d["CUSTOMER_x_PRODUCTGROUP_Sum_of_item_TotalCost_14d"]
customer_productgroup_sum_of_totalcost_14d.update_description(
    "Total spent by the customer on the product group over a 14d period."
)
customer_productgroup_sum_of_totalcost_28d = \
customer_productgroup_sum_of_totalcost_14d_28d["CUSTOMER_x_PRODUCTGROUP_Sum_of_item_TotalCost_28d"]
customer_productgroup_sum_of_totalcost_28d.update_description(
    "Total spent by the customer on the product group over a 28d period."
)
# See feature definition file
customer_productgroup_sum_of_totalcost_28d.definition

'# Generated by SDK version: 1.1.0.dev7\nfrom bson import ObjectId\nfrom featurebyte import DimensionTable\nfrom featurebyte import FeatureJobSetting\nfrom featurebyte import ItemTable\n\n\n# dimension_table name: "GROCERYPRODUCT"\ndimension_table = DimensionTable.get_by_id(ObjectId("666956c78080c62d0dc616e2"))\ndimension_view = dimension_table.get_view(\n    view_mode="manual", drop_column_names=[], column_cleaning_operations=[]\n)\n\n# item_table name: "INVOICEITEMS", event_table name: "GROCERYINVOICE"\nitem_table = ItemTable.get_by_id(ObjectId("666956c58080c62d0dc616e1"))\nitem_view = item_table.get_view(\n    event_suffix=None,\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[],\n    event_drop_column_names=["record_available_at"],\n    event_column_cleaning_operations=[],\n    event_join_column_names=[\n        "Timestamp",\n        "GroceryInvoiceGuid",\n        "GroceryCustomerGuid",\n        "tz_offset",\n    ],\n)\njoined_view = item_view.join(\n    dimension_view, on="GroceryProductGuid", how="left", rsuffix="", rprefix=""\n)\ngrouped = joined_view.groupby(\n    by_keys=["GroceryCustomerGuid", "ProductGroup"], category=None\n).aggregate_over(\n    value_column="TotalCost",\n    method="sum",\n    windows=["28d"],\n    feature_names=["CUSTOMER_x_PRODUCTGROUP_Sum_of_item_TotalCost_28d"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", period="3600s", offset="120s"\n    ),\n    skip_fill_na=True,\n    offset=None,\n)\nfeat = grouped["CUSTOMER_x_PRODUCTGROUP_Sum_of_item_TotalCost_28d"]\noutput = feat\noutput.save(_id=ObjectId("6669575033eb5cd5aebc1fe6"))\n'

In [21]:
# Add description
customer_latest_invoice_amount.update_description("Latest invoice Amount for the customer")
# See feature definition file
customer_latest_invoice_amount.definition

'# Generated by SDK version: 1.1.0.dev7\nfrom bson import ObjectId\nfrom featurebyte import ColumnCleaningOperation\nfrom featurebyte import DisguisedValueImputation\nfrom featurebyte import EventTable\nfrom featurebyte import FeatureJobSetting\nfrom featurebyte import ValueBeyondEndpointImputation\n\n\n# event_table name: "GROCERYINVOICE"\nevent_table = EventTable.get_by_id(ObjectId("666956c38080c62d0dc616e0"))\nevent_view = event_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[\n        ColumnCleaningOperation(\n            column_name="Amount",\n            cleaning_operations=[\n                DisguisedValueImputation(\n                    imputed_value=None, disguised_values=[-99.0, -98.0]\n                ),\n                ValueBeyondEndpointImputation(\n                    type="less_than", end_point=0.0, imputed_value=0.0\n                ),\n                ValueBeyondEndpointImputation(\n                    type="greater_than", end_point=2000.0, imputed_value=2000.0\n                ),\n            ],\n        )\n    ],\n)\ngrouped = event_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category=None\n).aggregate_over(\n    value_column="Amount",\n    method="latest",\n    windows=[None],\n    feature_names=["CUSTOMER_Latest_invoice_Amount"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", period="3600s", offset="120s"\n    ),\n    skip_fill_na=True,\n    offset=None,\n)\nfeat = grouped["CUSTOMER_Latest_invoice_Amount"]\noutput = feat\noutput.save(_id=ObjectId("6669575033eb5cd5aebc1fea"))\n'

In [22]:
# Add description
customer_count_of_invoice_14d = customer_count_of_invoice_14d_28d["CUSTOMER_Count_of_invoice_14d"]
customer_count_of_invoice_14d.update_description(
    "Count of invoice for the customer over a 14d period."
)
customer_count_of_invoice_28d = customer_count_of_invoice_14d_28d["CUSTOMER_Count_of_invoice_28d"]
customer_count_of_invoice_28d.update_description(
    "Count of invoice for the customer over a 28d period."
)
# See feature definition file
customer_count_of_invoice_28d.definition

'# Generated by SDK version: 1.1.0.dev7\nfrom bson import ObjectId\nfrom featurebyte import EventTable\nfrom featurebyte import FeatureJobSetting\n\n\n# event_table name: "GROCERYINVOICE"\nevent_table = EventTable.get_by_id(ObjectId("666956c38080c62d0dc616e0"))\nevent_view = event_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[],\n)\ngrouped = event_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category=None\n).aggregate_over(\n    value_column=None,\n    method="count",\n    windows=["28d"],\n    feature_names=["CUSTOMER_Count_of_invoice_28d"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", period="3600s", offset="120s"\n    ),\n    skip_fill_na=True,\n    offset=None,\n)\nfeat = grouped["CUSTOMER_Count_of_invoice_28d"]\noutput = feat\noutput.save(_id=ObjectId("6669575033eb5cd5aebc1fec"))\n'

In [23]:
# Add description
customer_avg_of_invoice_amount_14d = customer_avg_of_invoice_amount_14d_28d["CUSTOMER_Avg_of_invoice_Amount_14d"]
customer_avg_of_invoice_amount_14d.update_description(
    "Avg of invoice Amount for the customer over a 14d period."
)
customer_avg_of_invoice_amount_28d = customer_avg_of_invoice_amount_14d_28d["CUSTOMER_Avg_of_invoice_Amount_28d"]
customer_avg_of_invoice_amount_28d.update_description(
    "Avg of invoice Amount for the customer over a 28d period."
)
# See feature definition file
customer_avg_of_invoice_amount_28d.definition

'# Generated by SDK version: 1.1.0.dev7\nfrom bson import ObjectId\nfrom featurebyte import ColumnCleaningOperation\nfrom featurebyte import DisguisedValueImputation\nfrom featurebyte import EventTable\nfrom featurebyte import FeatureJobSetting\nfrom featurebyte import ValueBeyondEndpointImputation\n\n\n# event_table name: "GROCERYINVOICE"\nevent_table = EventTable.get_by_id(ObjectId("666956c38080c62d0dc616e0"))\nevent_view = event_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[\n        ColumnCleaningOperation(\n            column_name="Amount",\n            cleaning_operations=[\n                DisguisedValueImputation(\n                    imputed_value=None, disguised_values=[-99.0, -98.0]\n                ),\n                ValueBeyondEndpointImputation(\n                    type="less_than", end_point=0.0, imputed_value=0.0\n                ),\n                ValueBeyondEndpointImputation(\n                    type="greater_than", end_point=2000.0, imputed_value=2000.0\n                ),\n            ],\n        )\n    ],\n)\ngrouped = event_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category=None\n).aggregate_over(\n    value_column="Amount",\n    method="avg",\n    windows=["28d"],\n    feature_names=["CUSTOMER_Avg_of_invoice_Amount_28d"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", period="3600s", offset="120s"\n    ),\n    skip_fill_na=True,\n    offset=None,\n)\nfeat = grouped["CUSTOMER_Avg_of_invoice_Amount_28d"]\noutput = feat\noutput.save(_id=ObjectId("6669575033eb5cd5aebc1fee"))\n'

In [24]:
# Add description
customer_std_of_invoice_amount_14d = customer_std_of_invoice_amount_14d_28d["CUSTOMER_Std_of_invoice_Amount_14d"]
customer_std_of_invoice_amount_14d.update_description(
    "Std of invoice Amount for the customer over a 14d period."
)
customer_std_of_invoice_amount_28d = customer_std_of_invoice_amount_14d_28d["CUSTOMER_Std_of_invoice_Amount_28d"]
customer_std_of_invoice_amount_28d.update_description(
    "Std of invoice Amount for the customer over a 28d period."
)

# See feature definition file
customer_std_of_invoice_amount_28d.definition

'# Generated by SDK version: 1.1.0.dev7\nfrom bson import ObjectId\nfrom featurebyte import ColumnCleaningOperation\nfrom featurebyte import DisguisedValueImputation\nfrom featurebyte import EventTable\nfrom featurebyte import FeatureJobSetting\nfrom featurebyte import ValueBeyondEndpointImputation\n\n\n# event_table name: "GROCERYINVOICE"\nevent_table = EventTable.get_by_id(ObjectId("666956c38080c62d0dc616e0"))\nevent_view = event_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[\n        ColumnCleaningOperation(\n            column_name="Amount",\n            cleaning_operations=[\n                DisguisedValueImputation(\n                    imputed_value=None, disguised_values=[-99.0, -98.0]\n                ),\n                ValueBeyondEndpointImputation(\n                    type="less_than", end_point=0.0, imputed_value=0.0\n                ),\n                ValueBeyondEndpointImputation(\n                    type="greater_than", end_point=2000.0, imputed_value=2000.0\n                ),\n            ],\n        )\n    ],\n)\ngrouped = event_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category=None\n).aggregate_over(\n    value_column="Amount",\n    method="std",\n    windows=["28d"],\n    feature_names=["CUSTOMER_Std_of_invoice_Amount_28d"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", period="3600s", offset="120s"\n    ),\n    skip_fill_na=True,\n    offset=None,\n)\nfeat = grouped["CUSTOMER_Std_of_invoice_Amount_28d"]\noutput = feat\noutput.save(_id=ObjectId("6669575033eb5cd5aebc1ff0"))\n'

### Concepts in this tutorial
- [Aggregate Features](https://docs.featurebyte.com/latest/about/glossary/#aggregate-features)
- [Window Aggregate Features](https://docs.featurebyte.com/latest/about/glossary/#aggregates-over-a-window)

#### SDK reference for
- [View.groupby()](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.GroupByMixin.groupby/#see-also)
- [Groupby.aggregate_over()](https://docs.featurebyte.com/latest/reference/featurebyte.api.groupby.GroupBy.aggregate_over/)
- [List of aggregate functions](https://docs.featurebyte.com/latest/reference/featurebyte.enum.AggFunc/)
- [FeatureGroup](https://docs.featurebyte.com/latest/reference/core/feature_group/)
- [FeatureGroup.save()](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature_group.FeatureGroup.save/)